# Week VI - Radioactive Decay, 1D Random Walks and Duck Typing

## Simulating Radioactive Decay

In the following Python class we implement a simulator of radioactive decay for N isotopes.


In [ ]:
import numpy as np
import matplotlib.pyplot as plt

class radio_decay:
    '''
    This class simulates the radioactive decay
    of N isotopes
    '''
    
    def __init__(self,N_init,lamb):
        'Initialise the process'
        self.N_init = N_init
        self.lamb = lamb
        self.N = N_init
        self.rng = np.random.default_rng(seed=42424)
        self.step_counter = 0
        self.all_N = [N_init]
        print('Initial number of particles: {}, decay constant: {}'.format(self.N_init,self.lamb))
    
    def run_single_step(self):
        'Run a single random step for N particles'
        r = self.rng.random(self.N)
        self.N = self.N - sum(map(lambda x: True if (x <= self.lamb) else False, r))
        
    def run_steps(self,n_steps):
        'Run a number of random steps equal to n_steps'
        for i in range(n_steps):
            self.step_counter += 1
            print('Running step # {}'.format(self.step_counter))
            self.run_single_step()
            print('Number of particles: {}'.format(self.N))
            self.all_N.append(self.N)
    
    def visualize(self,logplot=False):
        if logplot:
            plt.semilogy(range(len(self.all_N)),self.all_N,'o-')
        else:
            plt.plot(range(len(self.all_N)),self.all_N,'o-')
        plt.xlabel('t')
        plt.ylabel('N')
        plt.show()
        
    def status(self):
        print('Current number of particles: {}, after {} steps'.format(self.N,self.step_counter))
        

In [ ]:
#Let's create an instance of the class
rd = radio_decay(10000,0.1)

In [ ]:
#Let's create an instance of the class
rd = radio_decay(10000,0.1)
#and evolve it for ten steps
rd.run_steps(10)

In [ ]:
#We inspect the status
rd.status()

In [ ]:
#Here we visualize data
rd.visualize()

In [ ]:
#and evolve it for 50 steps
rd.run_steps(50)

In [ ]:
rd.visualize()

In [ ]:
#Homework: try to fit the exponential and extract lambda
import matplotlib.pyplot as plt
plt.semilogy(range(len(rd.all_N)),rd.all_N,'o-')

-------------------------------------------------------

## 1D Random Walks

Next, we implement a Python class to simulate an ensemble of random walkers in one dimension

In [ ]:
import sys
import numpy as np 

class rw_1d:
    '''
    This class simulates the evolution
    of an ensamble of random walkers
    '''
    def __init__(self,N_steps,N_walkers,seeds = [42424],len_step=1):
        'Initialise the process'
        self.N_steps = N_steps
        self.N_walkers = N_walkers
        self.len_step = len_step
        if seeds == 'auto':
            seeds = range(self.N_walkers)
        else:
            if len(seeds)!=N_walkers:
                sys.exit('ERROR: seed length is not equal to number of random walkers')
        self.seeds = seeds
        self.rngs = [np.random.default_rng(seed=i) for i in self.seeds]
        print('Number of steps: {}, number of walkers: {}'.format(self.N_steps,self.N_walkers))
        self.x_trajs = []
        self.x_av = 0
        self.x2_av = 0
        self.var = 0
    
    def run_rw(self,rw_index):
        '''
        Evolve one random walker
        '''
        r = self.rngs[rw_index].random(self.N_steps)
        steps = list(map(lambda x: -1 if x<0.5 else 1, r))
        steps = np.array(steps)
        x = np.sum(steps)
        x2 = np.sum(steps)**2
        return x,x2,np.cumsum(steps)
    
    def run_many_rw(self):
        '''
        Evolve many random walkers
        '''
        x_l = []
        x2_l = []
        for i in range(self.N_walkers):
            x,x2,traj= self.run_rw(i)
            self.x_trajs.append(traj) 
            x_l.append(x)
            x2_l.append(x2)
        self.x_av = np.average(x_l)
        self.x2_av = np.average(x2_l)
        self.var  = self.x2_av - self.x_av**2


In [ ]:
r = rw_1d(N_steps=1000,N_walkers=100,seeds='auto')
r.run_many_rw()
print(r.x_av,r.x2_av,r.var)

In [ ]:
import matplotlib.pyplot as plt
plt.xlabel('steps')
plt.ylabel('$x$')
_ = [plt.plot(np.arange(r.N_steps),r.x_trajs[i],label='walker {}'.format(i+1)) for i in range(r.N_walkers)]
plt.legend()

In [ ]:
import matplotlib.pyplot as plt
a = np.array(r.x_trajs)**2
a = np.average(a,axis=0)
plt.xlabel('steps')
plt.ylabel('$x^2$')
_ = [plt.plot(np.arange(r.N_steps),r.x_trajs[i]**2) for i in range(r.N_walkers)]
plt.plot(np.arange(r.N_steps),a,'-',lw=2,c='r',label='average over walkers')
plt.plot(np.arange(r.N_steps),np.arange(r.N_steps),'-',lw=2,c='k',label='theory')
plt.legend()

-------------------------------------------------

## Duck Typing

> If it walks like a duck and it quacks like a duck, then it must be a duck.

Often, we do not really care about the type of an object but we are interested only in its behaviour. In particular, we typically need to know whether certain methods are implemented.

**Duck typing** is a form of polymorphims where functions operate on any object that implements the appropiate methods, regardless of their classes or explicit interface declarations (L. Ramalho, *Fluent Python*, O'Reilly, 2016).

Let us do some tests:

In [ ]:
iter??

In [ ]:
import numpy as np
def check_iterable(x):
    try:
        iter(x)
        print('{} is iterable'.format(x))
        return True
    except TypeError as err:
        print(err)
        return False
for x in [np.array([1,2,3]),[1,2,3],(1,2,3),'abcd',2]:
    check_iterable(x)
    

### Generators and the iterator protocol

In Python, there is a consistent way to iterate over sequences, no matter the specific object type. This happens thanks to an **iterator protocol**, which is a generic way to make objects iterable.
**Generators** allow to construct iterable objects, in a rather concise manner.


In [ ]:
range(10)

In [ ]:
np.arange(10)

In [ ]:
list(range(10))

In [ ]:
def gen_cube(N):
    for i in range(N):
        yield (i+1)**3
gen_cube(8)

In [ ]:
gen = gen_cube(8)

In [ ]:
for i in gen:
    print(i)

In [ ]:
for i in map(lambda x: x**2, [1,2,3]):
    print(i+2)

In [ ]:
map(lambda x: x**2, [1,2,3])